In [1]:
import json
from functools import partial
from typing import List

import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import seaborn as sns
from catboost import CatBoostClassifier, Pool
from catboost.utils import eval_metric
from scipy.spatial.distance import cosine, euclidean
from sklearn.metrics import pairwise_distances
from sklearn.model_selection import train_test_split

from sklearn.metrics import precision_score


### Load data

In [2]:
dataset = pd.read_parquet(r"C:\Users\druzh\Project_python\ozon_top_1\Datasets/train_pairs.parquet")
etl = pd.read_parquet(r"C:\Users\druzh\Project_python\ozon_top_1\Datasets/train_data.parquet")

In [3]:
dataset.head(2)

target  variantid1  variantid2
0     0.0    51197862    51198054
1     1.0    53062686   536165289

In [4]:
dataset["target"].value_counts()

0.0    171527
1.0    135013
Name: target, dtype: int64

In [5]:
etl.head(2)

variantid                                               name  \
0   51195767  Удлинитель Партнер-Электро ПВС 2х0,75 ГОСТ,6A,...   
1   53565809  Магнитный кабель USB 2.0 A (m) - USB Type-C (m...   

                                          categories color_parsed  \
0  {"1": "EPG", "2": "Электроника", "3": "Сетевые...  [оранжевый]   
1  {"1": "EPG", "2": "Электроника", "3": "Кабели ...    [красный]   

                            pic_embeddings_resnet_v1  \
0                                               None   
1  [[0.26863545, -0.3130674, 0.29023397, 0.073978...   

                       main_pic_embeddings_resnet_v1  \
0  [[0.04603629, 0.18839523, -0.09973055, -0.6636...   
1  [[1.1471839, -0.665361, 0.7745614, 0.26716197,...   

                                        name_bert_64  \
0  [-0.47045058, 0.67237014, 0.48984158, -0.54485...   
1  [-0.6575592, 0.6522429, 0.5426037, -0.54347897...   

                   characteristic_attributes_mapping  
0  {"Номинальный ток, А":["10"],"Цвет товара":["о...  
1  {"Конструктивные особенности":["Магнитная конс...

In [6]:
print(etl.shape, dataset.shape)

(457063, 8) (306540, 3)


Get raw data for each variantid.

In [7]:
features0 = (
    dataset
    .merge(
        etl
        .add_suffix('1'),
        on="variantid1"
    )
    .merge(
        etl
        .add_suffix('2'),
        on="variantid2"
    )
)

In [8]:
features0.head(2)

target  variantid1  variantid2  \
0     0.0    51197862    51198054   
1     0.0    51197862    51199884   

                                               name1  \
0  Удлинитель TDM Electric Люкс УЛ05В 5 м (SQ1303...   
1  Удлинитель TDM Electric Люкс УЛ05В 5 м (SQ1303...   

                                         categories1 color_parsed1  \
0  {"1": "EPG", "2": "Электроника", "3": "Сетевые...       [белый]   
1  {"1": "EPG", "2": "Электроника", "3": "Сетевые...       [белый]   

  pic_embeddings_resnet_v11  \
0                      None   
1                      None   

                      main_pic_embeddings_resnet_v11  \
0  [[-0.4304909, -0.49474272, -0.46439183, -0.060...   
1  [[-0.4304909, -0.49474272, -0.46439183, -0.060...   

                                       name_bert_641  \
0  [-0.5104684, 0.56158644, 0.58873796, -0.529718...   
1  [-0.5104684, 0.56158644, 0.58873796, -0.529718...   

                  characteristic_attributes_mapping1  \
0  {"Число жил":["3"],"Макс. нагрузка, Вт":["3500...   
1  {"Число жил":["3"],"Макс. нагрузка, Вт":["3500...   

                                               name2  \
0  Удлинитель TDM Electric Люкс УЛ05В 1.5 м (SQ13...   
1  Удлинитель TDM Electric Люкс УЛ05В 3 м (SQ1303...   

                                         categories2 color_parsed2  \
0  {"1": "EPG", "2": "Электроника", "3": "Сетевые...       [белый]   
1  {"1": "EPG", "2": "Электроника", "3": "Сетевые...       [белый]   

  pic_embeddings_resnet_v12  \
0                      None   
1                      None   

                      main_pic_embeddings_resnet_v12  \
0  [[-0.42941108, -0.5129398, -0.4753536, -0.0677...   
1  [[-0.43180764, -0.49580905, -0.5062628, -0.130...   

                                       name_bert_642  \
0  [-0.455473, 0.58157134, 0.5870387, -0.5325003,...   
1  [-0.5425725, 0.6415736, 0.51481575, -0.5687392...   

                  characteristic_attributes_mapping2  
0  {"Электробезопасность":["Заземление"],"Длина к...  
1  {"Макс. нагрузка, Вт":["3500"],"Стандарт защит...

In [9]:
def get_pic_features(main_pic_embeddings_1,
                     main_pic_embeddings_2,
                     percentiles: List[int]):
    """Calculate distances percentiles for 
    pairwise pic distances. Percentiles are useful 
    when product has several pictures.
    """
    
    if main_pic_embeddings_1 is not None and main_pic_embeddings_2 is not None:
        main_pic_embeddings_1 = np.array([x for x in main_pic_embeddings_1])
        main_pic_embeddings_2 = np.array([x for x in main_pic_embeddings_2])
        
        dist_m = pairwise_distances(
            main_pic_embeddings_1, main_pic_embeddings_2
        )
    else:
        dist_m = np.array([[-1]])

    pair_features = []
    pair_features += np.percentile(dist_m, percentiles).tolist()

    return pair_features


def text_dense_distances(ozon_embedding, comp_embedding):
    """Calculate Euclidean and Cosine distances between
    ozon_embedding and comp_embedding.
    """
    pair_features = []
    if ozon_embedding is None or comp_embedding is None:
        pair_features = [-1, -1]
    elif len(ozon_embedding) == 0 or len(comp_embedding) == 0:
        pair_features = [-1, -1]
    else:
        pair_features.append(
            euclidean(ozon_embedding, comp_embedding)
        )
        cosine_value = cosine(ozon_embedding, comp_embedding)
        
        pair_features.append(cosine_value)

    return pair_features

Features functions.

In [10]:
features = features0

In [11]:
get_pic_features_func = partial(
    get_pic_features,
    percentiles=[0, 25, 50]
)

In [12]:
features[["pic_dist_0_perc", "pic_dist_25_perc", "pic_dist_50_perc"]] = (
    features[["pic_embeddings_resnet_v11", "pic_embeddings_resnet_v12"]].apply(
        lambda x: pd.Series(get_pic_features_func(*x)), axis=1
    )
)

# btw try to add distances between main pic embs

In [13]:
features[["main_pic_dist_0_perc", "main_pic_dist_25_perc", "main_pic_dist_50_perc"]] = (
    features[["main_pic_embeddings_resnet_v11", "main_pic_embeddings_resnet_v12"]].apply(
        lambda x: pd.Series(get_pic_features_func(*x)), axis=1
    )
)

In [14]:
features[["euclidean_name_bert_dist", "cosine_name_bert_dist"]] = (
    features[["name_bert_641", "name_bert_642"]].apply(
        lambda x: pd.Series(text_dense_distances(*x)), axis=1
    )
)

# try to use your favorite NLP model

In [15]:
features["cat31"] = features["categories1"].apply(lambda x: json.loads(x)["3"])
cat3_counts = features["cat31"].value_counts().to_dict()

In [16]:
features["cat31_grouped"] = features["cat31"].apply(lambda x: x if cat3_counts[x] > 1000 else "rest")

In [17]:
features["cat32"] = features["categories2"].apply(lambda x: json.loads(x)["3"])
cat3_counts = features["cat32"].value_counts().to_dict()

In [18]:
features["cat32_grouped"] = features["cat32"].apply(lambda x: x if cat3_counts[x] > 1000 else "rest")

In [19]:
from sklearn.feature_extraction.text import CountVectorizer

def create_top_bag_of_words(sentences, top_words):
    vectorizer = CountVectorizer(max_features=top_words)
    bag_of_words = vectorizer.fit_transform(sentences)
    len_sentences = [len(sentence.split()) for sentence in sentences]

    return bag_of_words, len_sentences, vectorizer

def encode_sentences(sentences, vectorizer):
    encoded_sentences = vectorizer.transform(sentences)
    len_sentences = [len(sentence.split()) for sentence in sentences]
    feature_names = vectorizer.get_feature_names()

    decoded_sentences = []
    for encoded_sentence in encoded_sentences:
        decoded_sentence = [feature_names[i] for i in encoded_sentence.indices]
        decoded_sentences.append(decoded_sentence)

    return decoded_sentences, len_sentences

In [20]:
bag_of_words, len_sentences, names_bag_vectorizer = create_top_bag_of_words(np.hstack((features['name1'].values, features['name2'].values)), 5000)

In [21]:
bag_of_words = bag_of_words.toarray()

In [17]:
print(bag_of_words)

[[0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 ...
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]]


In [22]:
features["name1_bag"] = bag_of_words[:len(bag_of_words) // 2].tolist()

In [23]:
features["name2_bag"] = bag_of_words[len(bag_of_words) // 2:].tolist()

In [24]:
features["name1_len"] = len_sentences[:len(len_sentences) // 2]

In [25]:
features["name2_len"] = len_sentences[len(len_sentences) // 2:]

In [26]:
bag_of_words, len_sentences, cats_bag_vectorizer = create_top_bag_of_words(np.hstack((features['cat31'].values, features['cat32'].values)), 250)

In [27]:
bag_of_words = bag_of_words.toarray()

In [28]:
features["cat31_bag"] = bag_of_words[:len(bag_of_words) // 2].tolist()

In [29]:
features = features.drop(
        ["name1", "categories1", "pic_embeddings_resnet_v11", "main_pic_embeddings_resnet_v11", "name_bert_641",
         "name2",
         "categories2", "pic_embeddings_resnet_v12", "main_pic_embeddings_resnet_v12", "name_bert_642", 'characteristic_attributes_mapping1', 'characteristic_attributes_mapping2'], axis=1)
features = features.drop(['cat31', 'cat32'], axis=1)

In [30]:
features["cat32_bag"] =  bag_of_words[len(bag_of_words) // 2:].tolist()

In [31]:
features["cat31_len"] = len_sentences[:len(len_sentences) // 2]

In [32]:
features["cat32_len"] = len_sentences[len(len_sentences) // 2:]

In [33]:
features.head(2)

target  variantid1  variantid2 color_parsed1 color_parsed2  \
0     0.0    51197862    51198054       [белый]       [белый]   
1     0.0    51197862    51199884       [белый]       [белый]   

   pic_dist_0_perc  pic_dist_25_perc  pic_dist_50_perc  main_pic_dist_0_perc  \
0             -1.0              -1.0              -1.0              0.259265   
1             -1.0              -1.0              -1.0              0.282023   

   main_pic_dist_25_perc  ...                               cat31_grouped  \
0               0.259265  ...  Сетевые фильтры, разветвители и удлинители   
1               0.282023  ...  Сетевые фильтры, разветвители и удлинители   

                                cat32_grouped  \
0  Сетевые фильтры, разветвители и удлинители   
1  Сетевые фильтры, разветвители и удлинители   

                                           name1_bag  \
0  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
1  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   

                                           name2_bag name1_len name2_len  \
0  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...         8         8   
1  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...         8         8   

                                           cat31_bag  \
0  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
1  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   

                                           cat32_bag  cat31_len cat32_len  
0  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...          5         5  
1  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...          5         5  

[2 rows x 23 columns]

In [34]:
color_1_prod = features['color_parsed1'].values
colors = []
for i in range(len(color_1_prod)):
    try:
        colors.append(color_1_prod[i][0])
    except:
        colors.append('None')
color_2_prod = features['color_parsed2'].values
for j in range(len(color_2_prod)):
    try:
        colors.append(color_2_prod[j][0])
    except:
        colors.append('None')

In [35]:
bag_of_words, len_sentences, colors_bag_vectorizer = create_top_bag_of_words(colors, 200)

In [36]:
bag_of_words.shape

(613080, 177)

In [37]:
bag_of_words = bag_of_words.toarray()

In [38]:
features["color1_bag"] = bag_of_words[:len(bag_of_words) // 2].tolist()

In [39]:
features["color2_bag"] =  bag_of_words[len(bag_of_words) // 2:].tolist()

In [40]:
features = features.drop(
        ["color_parsed1", "color_parsed2"], axis=1)

In [41]:
features.head(2)

target  variantid1  variantid2  pic_dist_0_perc  pic_dist_25_perc  \
0     0.0    51197862    51198054             -1.0              -1.0   
1     0.0    51197862    51199884             -1.0              -1.0   

   pic_dist_50_perc  main_pic_dist_0_perc  main_pic_dist_25_perc  \
0              -1.0              0.259265               0.259265   
1              -1.0              0.282023               0.282023   

   main_pic_dist_50_perc  euclidean_name_bert_dist  ...  \
0               0.259265                  0.338458  ...   
1               0.282023                  0.475419  ...   

                                           name1_bag  \
0  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
1  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   

                                           name2_bag name1_len name2_len  \
0  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...         8         8   
1  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...         8         8   

                                           cat31_bag  \
0  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
1  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   

                                           cat32_bag  cat31_len cat32_len  \
0  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...          5         5   
1  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...          5         5   

                                          color1_bag  \
0  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
1  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   

                                          color2_bag  
0  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
1  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  

[2 rows x 23 columns]

In [42]:
feats = ["name1_bag", "name1_len", "name2_bag", "name2_len", "cat31_bag", "cat32_bag", "cat31_len", "cat32_len", "color1_bag", 'color2_bag', "pic_dist_0_perc", "pic_dist_25_perc", "pic_dist_50_perc", "main_pic_dist_0_perc", "main_pic_dist_25_perc", "main_pic_dist_50_perc", "euclidean_name_bert_dist", "cosine_name_bert_dist"]

In [43]:
X_train, X_test = train_test_split(
    features[feats + ["target", "variantid1", "variantid2", "cat31_grouped"]], 
    test_size=0.1, random_state=42, stratify=features[["target"]])

X_train, X_val = train_test_split(
    X_train[feats + ["target"]], 
    test_size=0.1, random_state=42, stratify=X_train[["target"]])

cats = X_test["cat31_grouped"]
y_test_w_var = X_test[["target", "variantid1", "variantid2"]]
y_test = X_test[["target"]]

X_test = X_test.drop(["target", "variantid1", "variantid2", "cat31_grouped"], axis=1)

y_train = X_train["target"]
y_val = X_val["target"]
 
X_train = X_train.drop(["target"], axis=1)
X_val = X_val.drop(["target"], axis=1)

        


In [44]:
cats

289251                                       rest
268549                                      Чехол
204513                                  Компьютер
142696                                  Компьютер
75368     Смартфоны, планшеты, мобильные телефоны
                           ...                   
267455    Жесткие диски, SSD и сетевые накопители
67274                                   Компьютер
18945                                       Чехол
42843                                   Компьютер
162254                   Батарейки и аккумуляторы
Name: cat31_grouped, Length: 30654, dtype: object

In [ ]:
X_train_final = []

for i in range(len(X_train)):
    row = []
    row.extend(list(X_train[feats[0]].iloc[i]))
    row.extend(list(X_train[feats[2]].iloc[i]))
    row.extend(list(X_train[feats[4]].iloc[i]))
    row.extend(list(X_train[feats[5]].iloc[i]))
    row.extend(list(X_train[feats[8]].iloc[i]))
    row.extend(list(X_train[feats[9]].iloc[i]))
    row.extend([X_train[feats[b]].iloc[i] for b in [1,3,6,7,8,9,10,11,12,13,14,15]])
    X_train_final.append(row)

In [ ]:
print(len(X_train_final))

In [ ]:
print(y_train)

In [ ]:
X_test_final = []

for i in range(len(X_test)):
    row = []
    row.extend(list(X_test[feats[0]].iloc[i]))
    row.extend(list(X_test[feats[2]].iloc[i]))
    row.extend(list(X_test[feats[4]].iloc[i]))
    row.extend(list(X_test[feats[5]].iloc[i]))
    row.extend(list(X_test[feats[8]].iloc[i]))
    row.extend(list(X_test[feats[9]].iloc[i]))
    row.extend([X_test[feats[b]].iloc[i] for b in [1,3,6,7,8,9,10,11,12,13,14,15]])
    X_test_final.append(row)

In [ ]:
print(len(X_test_final))

In [ ]:
print(y_test)

In [43]:
from sklearn.linear_model import SGDClassifier

def train_logistic_regression(X, y, chunk_size, num_epochs=10):
    clf = SGDClassifier(loss='log')  # Используем логистическую регрессию
    num_samples = len(X)
    num_chunks = num_samples // chunk_size

    for epoch in range(num_epochs):
        print(epoch)
        for chunk_idx in range(num_chunks):
            start_idx = chunk_idx * chunk_size
            end_idx = start_idx + chunk_size
            X_chunk = X[start_idx:end_idx]
            y_chunk = y[start_idx:end_idx]
            clf.partial_fit(X_chunk, y_chunk, classes=np.unique(y))
    
    return clf

In [54]:
chunk_size = 10000
num_epochs = 500

model = train_logistic_regression(X_train_final, y_train, chunk_size, num_epochs)

0


C:\Users\druzh\AppData\Local\Temp\ipykernel_11748\132693369.py:14: FutureWarning: The behavior of `series[i:j]` with an integer-dtype index is deprecated. In a future version, this will be treated as *label-based* indexing, consistent with e.g. `series[i]` lookups. To retain the old behavior, use `series.iloc[i:j]`. To get the future behavior, use `series.loc[i:j]`.
  y_chunk = y[start_idx:end_idx]
C:\Users\druzh\Project_python\venv\lib\site-packages\sklearn\linear_model\_stochastic_gradient.py:163: FutureWarning: The loss 'log' was deprecated in v1.1 and will be removed in version 1.3. Use `loss='log_loss'` which is equivalent.
  warnings.warn(
C:\Users\druzh\AppData\Local\Temp\ipykernel_11748\132693369.py:14: FutureWarning: The behavior of `series[i:j]` with an integer-dtype index is deprecated. In a future version, this will be treated as *label-based* indexing, consistent with e.g. `series[i]` lookups. To retain the old behavior, use `series.iloc[i:j]`. To get the future behavior, 

C:\Users\druzh\AppData\Local\Temp\ipykernel_11748\132693369.py:14: FutureWarning: The behavior of `series[i:j]` with an integer-dtype index is deprecated. In a future version, this will be treated as *label-based* indexing, consistent with e.g. `series[i]` lookups. To retain the old behavior, use `series.iloc[i:j]`. To get the future behavior, use `series.loc[i:j]`.
  y_chunk = y[start_idx:end_idx]
C:\Users\druzh\AppData\Local\Temp\ipykernel_11748\132693369.py:14: FutureWarning: The behavior of `series[i:j]` with an integer-dtype index is deprecated. In a future version, this will be treated as *label-based* indexing, consistent with e.g. `series[i]` lookups. To retain the old behavior, use `series.iloc[i:j]`. To get the future behavior, use `series.loc[i:j]`.
  y_chunk = y[start_idx:end_idx]
C:\Users\druzh\AppData\Local\Temp\ipykernel_11748\132693369.py:14: FutureWarning: The behavior of `series[i:j]` with an integer-dtype index is deprecated. In a future version, this will be treated

1


C:\Users\druzh\AppData\Local\Temp\ipykernel_11748\132693369.py:14: FutureWarning: The behavior of `series[i:j]` with an integer-dtype index is deprecated. In a future version, this will be treated as *label-based* indexing, consistent with e.g. `series[i]` lookups. To retain the old behavior, use `series.iloc[i:j]`. To get the future behavior, use `series.loc[i:j]`.
  y_chunk = y[start_idx:end_idx]
C:\Users\druzh\AppData\Local\Temp\ipykernel_11748\132693369.py:14: FutureWarning: The behavior of `series[i:j]` with an integer-dtype index is deprecated. In a future version, this will be treated as *label-based* indexing, consistent with e.g. `series[i]` lookups. To retain the old behavior, use `series.iloc[i:j]`. To get the future behavior, use `series.loc[i:j]`.
  y_chunk = y[start_idx:end_idx]
C:\Users\druzh\AppData\Local\Temp\ipykernel_11748\132693369.py:14: FutureWarning: The behavior of `series[i:j]` with an integer-dtype index is deprecated. In a future version, this will be treated

...

C:\Users\druzh\AppData\Local\Temp\ipykernel_11748\132693369.py:14: FutureWarning: The behavior of `series[i:j]` with an integer-dtype index is deprecated. In a future version, this will be treated as *label-based* indexing, consistent with e.g. `series[i]` lookups. To retain the old behavior, use `series.iloc[i:j]`. To get the future behavior, use `series.loc[i:j]`.
  y_chunk = y[start_idx:end_idx]
C:\Users\druzh\AppData\Local\Temp\ipykernel_11748\132693369.py:14: FutureWarning: The behavior of `series[i:j]` with an integer-dtype index is deprecated. In a future version, this will be treated as *label-based* indexing, consistent with e.g. `series[i]` lookups. To retain the old behavior, use `series.iloc[i:j]`. To get the future behavior, use `series.loc[i:j]`.
  y_chunk = y[start_idx:end_idx]
C:\Users\druzh\AppData\Local\Temp\ipykernel_11748\132693369.py:14: FutureWarning: The behavior of `series[i:j]` with an integer-dtype index is deprecated. In a future version, this will be treated

C:\Users\druzh\AppData\Local\Temp\ipykernel_11748\132693369.py:14: FutureWarning: The behavior of `series[i:j]` with an integer-dtype index is deprecated. In a future version, this will be treated as *label-based* indexing, consistent with e.g. `series[i]` lookups. To retain the old behavior, use `series.iloc[i:j]`. To get the future behavior, use `series.loc[i:j]`.
  y_chunk = y[start_idx:end_idx]
C:\Users\druzh\AppData\Local\Temp\ipykernel_11748\132693369.py:14: FutureWarning: The behavior of `series[i:j]` with an integer-dtype index is deprecated. In a future version, this will be treated as *label-based* indexing, consistent with e.g. `series[i]` lookups. To retain the old behavior, use `series.iloc[i:j]`. To get the future behavior, use `series.loc[i:j]`.
  y_chunk = y[start_idx:end_idx]
C:\Users\druzh\AppData\Local\Temp\ipykernel_11748\132693369.py:14: FutureWarning: The behavior of `series[i:j]` with an integer-dtype index is deprecated. In a future version, this will be treated

499


C:\Users\druzh\AppData\Local\Temp\ipykernel_11748\132693369.py:14: FutureWarning: The behavior of `series[i:j]` with an integer-dtype index is deprecated. In a future version, this will be treated as *label-based* indexing, consistent with e.g. `series[i]` lookups. To retain the old behavior, use `series.iloc[i:j]`. To get the future behavior, use `series.loc[i:j]`.
  y_chunk = y[start_idx:end_idx]
C:\Users\druzh\AppData\Local\Temp\ipykernel_11748\132693369.py:14: FutureWarning: The behavior of `series[i:j]` with an integer-dtype index is deprecated. In a future version, this will be treated as *label-based* indexing, consistent with e.g. `series[i]` lookups. To retain the old behavior, use `series.iloc[i:j]`. To get the future behavior, use `series.loc[i:j]`.
  y_chunk = y[start_idx:end_idx]
C:\Users\druzh\AppData\Local\Temp\ipykernel_11748\132693369.py:14: FutureWarning: The behavior of `series[i:j]` with an integer-dtype index is deprecated. In a future version, this will be treated

C:\Users\druzh\AppData\Local\Temp\ipykernel_11748\132693369.py:14: FutureWarning: The behavior of `series[i:j]` with an integer-dtype index is deprecated. In a future version, this will be treated as *label-based* indexing, consistent with e.g. `series[i]` lookups. To retain the old behavior, use `series.iloc[i:j]`. To get the future behavior, use `series.loc[i:j]`.
  y_chunk = y[start_idx:end_idx]
C:\Users\druzh\AppData\Local\Temp\ipykernel_11748\132693369.py:14: FutureWarning: The behavior of `series[i:j]` with an integer-dtype index is deprecated. In a future version, this will be treated as *label-based* indexing, consistent with e.g. `series[i]` lookups. To retain the old behavior, use `series.iloc[i:j]`. To get the future behavior, use `series.loc[i:j]`.
  y_chunk = y[start_idx:end_idx]
C:\Users\druzh\AppData\Local\Temp\ipykernel_11748\132693369.py:14: FutureWarning: The behavior of `series[i:j]` with an integer-dtype index is deprecated. In a future version, this will be treated

In [60]:
import random
from sklearn.metrics import mean_squared_error
from sklearn.metrics import f1_score
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, precision_score, recall_score
prediction = model.predict(X_test_final)

mse = mean_squared_error(y_test.T, prediction)
print("Mean Squared Error:", mse)

f1 = f1_score(y_test.T, prediction)
print("f1:", f1)

accuracy = accuracy_score(y_test.T, prediction)
precision = precision_score(y_test.T, prediction)
recall = recall_score(y_test.T, prediction)
print("Accuracy:", accuracy)
print("Precision:", precision)
print("Recall:", recall)

Mean Squared Error: 0.23615188882364455
f1: 0.7342998715360617
Accuracy: 0.7638481111763554
Precision: 0.7278084982537835
Recall: 0.7409080808828976


In [56]:
import joblib

joblib.dump(model, 'logistic_regression_model_500_epochs.pkl')

['logistic_regression_model_500_epochs.pkl']

In [61]:
import numpy as np
from sklearn.metrics import precision_recall_curve, auc


def pr_auc_macro(
    y_true: pd.Series,
    y_pred: pd.Series,
    categories: pd.Series,
    prec_level: float = 0.75
) -> float:
    
    weights = []
    pr_aucs = []

    unique_cats, counts = np.unique(categories, return_counts=True)
    for i, category in enumerate(unique_cats):
        cat_idx = np.where(categories == category)[0]
        print(cat_idx)
        y_pred_cat = y_pred[cat_idx]
        y_true_cat = y_true[cat_idx]
        y_true_cat = y_true_cat.T 
        y, x, thr = precision_recall_curve(y_true_cat, y_pred_cat)
        gt_prec_level_idx = np.where(y >= prec_level)[0]

        try:
            pr_auc_prec_level = auc(x[gt_prec_level_idx], y[gt_prec_level_idx])
            if not np.isnan(pr_auc_prec_level):
                pr_aucs.append(pr_auc_prec_level)
                weights.append(counts[i] / len(categories))
        except ValueError as err:
            pr_aucs.append(0)
            weights.append(0)
    return np.average(pr_aucs, weights=weights)

In [62]:
X_test["scores"] = prediction
y_pred = X_test["scores"]
y_test = y_test.reset_index(drop = True)
y_pred = y_pred.reset_index(drop = True)
cats = cats.reset_index(drop = True)
y_test = y_test.T

In [63]:
pr_auc_macro_metr = pr_auc_macro(
    y_true=y_test, 
    y_pred=y_pred,
    categories = cats,
    prec_level=0.75
)

pr_auc_macro_metr

[    0    89    98 ... 30512 30533 30551]


KeyError: '[89, 98, 158, 181, 203, 204, 220, 222, 229, 259, 289, 321, 379, 407, 422, 446, 450, 467, 488, 497, 513, 524, 557, 573, 589, 620, 635, 639, 655, 656, 666, 671, 678, 749, 770, 795, 850, 863, 913, 947, 954, 1008, 1009, 1062, 1065, 1114, 1136, 1153, 1174, 1184, 1202, 1214, 1241, 1248, 1266, 1268, 1274, 1308, 1391, 1418, 1442, 1447, 1479, 1491, 1622, 1623, 1632, 1656, 1698, 1700, 1721, 1734, 1766, 1785, 1810, 1855, 1945, 2020, 2050, 2114, 2232, 2261, 2272, 2280, 2283, 2294, 2340, 2408, 2413, 2419, 2476, 2491, 2508, 2547, 2556, 2559, 2581, 2603, 2609, 2627, 2638, 2649, 2659, 2719, 2728, 2733, 2789, 2791, 2807, 2840, 2894, 2907, 2965, 2970, 3003, 3005, 3008, 3011, 3021, 3034, 3046, 3117, 3163, 3168, 3171, 3228, 3253, 3307, 3335, 3353, 3367, 3373, 3382, 3466, 3512, 3530, 3552, 3561, 3638, 3641, 3699, 3712, 3721, 3731, 3789, 3807, 3813, 3823, 3852, 3872, 3937, 3994, 4012, 4021, 4062, 4063, 4126, 4277, 4286, 4291, 4303, 4310, 4316, 4317, 4357, 4389, 4432, 4449, 4468, 4498, 4576, 4597,

In [64]:
precision, recall, thrs = precision_recall_curve(y_test.T, y_pred)
pr_auc = auc(recall, precision)

fig, ax1 = plt.subplots(1)

ax1.plot( recall , precision)
ax1.axhline(y=0.75, color='grey', linestyle='-');

ValueError: multilabel-indicator format is not supported